In [1]:
import os

In [2]:
os.chdir('/home/xiaochen/kewen/IF_project')

In [3]:

import argparse
import os
import random
from matplotlib import pyplot as plt
from sklearn.utils import shuffle
from tqdm import tqdm
import copy

import numpy as np
import torch

from torchvision import models, transforms
from src.data_utils.MnistDataset import MnistDataset
from src.utils.utils import save_json
from src.data_utils.Cifar10Dataset import Cifar10Dataset
from src.solver.hessian_solver import hessianSolver
from src.modeling.classification_models import CnnCifar, MNIST_1, CnnMnist, MNIST_LogisticRegression, MNIST_2
from src.modeling.influence_models import Net_IF, MNIST_IF_1
from torch.autograd.functional import hessian
from torch.nn.utils import _stateless
from torch.nn import CrossEntropyLoss 
import yaml

/home/xiaochen/anaconda3/envs/IFv2/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
YAMLPath = 'src/config/MNIST/single_test/exp/MNIST_1_100each/test_id_1/fenchel.yaml'


In [5]:
%env CUDA_VISIBLE_DEVICES=2

env: CUDA_VISIBLE_DEVICES=2


In [6]:
class Struct:
    def __init__(self, **entries):
        self.__dict__.update(entries)

def get_single_from_dataset(dataset, idx):
        x, y = dataset[idx]
        x = x.unsqueeze(0)
        y = torch.LongTensor([y])
        return x, y

In [7]:
    parser = argparse.ArgumentParser()
    parser.add_argument("--YAMLPath", type=str)
    args, unknown = parser.parse_known_args()
    if args.YAMLPath:
        YAMLPath = args.YAMLPath
    with open(YAMLPath) as file:
        config = yaml.safe_load(file)
    args = Struct(**config)

In [8]:
torch.manual_seed(args.seed)
torch.cuda.manual_seed(args.seed)
np.random.seed(args.seed)
random.seed(args.seed)
torch.backends.cudnn.deterministic=True



if args.dataset_name == 'cifar10':
    Dataset = Cifar10Dataset
    trans = transforms.Compose([ 
        transforms.ToTensor(), 
        transforms.Normalize(
        (0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
        ])
elif args.dataset_name == 'mnist':
    Dataset = MnistDataset
    trans = transforms.Compose([ 
        transforms.ToTensor(), 
        transforms.Normalize(
        (0.1307,),(0.3081,))
        ])
else:
    raise NotImplementedError()

class_label_dict = Dataset.get_class_label_dict()
train_classes = [class_label_dict[c] for c in args.train_classes]
ImageDataset = Dataset(args.dev_original_folder, args.dev_transformed_folder, args.test_original_folder, args.test_transformed_folder, train_classes, trans, args.num_per_class)

if args.classification_model == 'MNIST_1':
    classification_model = MNIST_1(args._hidden_size_classification, args._num_class).to('cuda')
elif args.classification_model == 'MNIST_2':
    classification_model = MNIST_2(args._num_class).to('cuda')
elif args.classification_model == 'MNIST_LogisticRegression':
    classification_model = MNIST_LogisticRegression(args._num_class).to('cuda')
elif args.classification_model == 'CnnMnist':
    classification_model = CnnMnist(args._num_class).to('cuda')
else:
    raise NotImplementedError()

train_dataset, train_dataset_no_transform = ImageDataset.get_train()
dev_dataset, dev_dataset_no_transform = ImageDataset.get_dev()

x_dev, y_dev = get_single_from_dataset(
    dev_dataset, args.dev_id_num)
train_dataset_size = len(train_dataset)

ckpt_dir = os.path.join("checkpoints/fenchel", args.dataset_name, args.classification_model)
os.makedirs(ckpt_dir, exist_ok=True)
pretrain_ckpt_path = os.path.join(ckpt_dir,
f"epoch{args.max_pretrain_epoch}_lr{args.pretrain_classification_lr}_" + args._pretrain_ckpt_name )
inv_hessian_path = os.path.join(ckpt_dir, "numpy_inv_hessian_" + os.path.basename(pretrain_ckpt_path))
hessian_solver = hessianSolver(classification_model, pretrain_ckpt_path, inv_hessian_path)
hessian_solver.load_data('train', train_dataset, 32, shuffle= True)
hessian_solver.load_data('dev', dev_dataset, 32, shuffle= False)

        

number of examples with label '0': 100
number of examples with label '1': 100
number of examples with label '2': 100
number of examples with label '3': 100
number of examples with label '4': 100
number of examples with label '5': 100
number of examples with label '6': 100
number of examples with label '7': 100
number of examples with label '8': 100
number of examples with label '9': 100
loaded train_dataset with 1000 samples
loaded dev FolderDataset with 10 files in folder, 


In [9]:
hessian_solver.get_optimizer_classification(
args.classification_lr,
args.classification_momentum,
args.classification_weight_decay,
args.optimizer_classification)


In [10]:
for epoch in tqdm(range(10000)):
    hessian_solver.pretrain_epoch()
    dev_acc = hessian_solver.evaluate('dev')
#     print('Pre-train Epoch {}, dev Acc: {:.4f}'.format(
#         epoch, 100. * dev_acc))
hessian_solver.save_checkpoint_classification(pretrain_ckpt_path)

Training Epoch:   0%|                                                                                                      | 0/32 [00:00<?, ?it/s]
                                                                                                                                                  
Training Epoch: 100%|█████████████████████████████████████████████████████████████████████████████████████████████| 32/32 [00:00<00:00, 32.16it/s]


[20] loss: 1.034 



  0%|                                                                                                         | 1/10000 [00:01<2:47:28,  1.00s/it]
                                                                                                                                                  
  0%|                                                                                                         | 1/10000 [00:01<2:47:28,  1.00s/it]
                                                                                                                                                  
Training Epoch: 100%|████████████████████████████████████████████████████████████████████████████████████████████| 32/32 [00:00<00:00, 458.95it/s]


[40] loss: 0.696 
[60] loss: 0.639 



Evaluating dev set: 100%|██████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 509.14it/s]

                                                                                                                                                  
Training Epoch: 100%|████████████████████████████████████████████████████████████████████████████████████████████| 32/32 [00:00<00:00, 681.26it/s]


...


Evaluating dev set: 100%|█████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00, 1117.29it/s]

                                                                                                                                                  
100%|███████████████████████████████████████████████████████████████████████████████████████████████████████▉| 9997/10000 [10:12<00:00, 18.22it/s]
                                                                                                                                                  


[319980] loss: 0.041 


Training Epoch: 100%|████████████████████████████████████████████████████████████████████████████████████████████| 32/32 [00:00<00:00, 763.73it/s]


[320000] loss: 0.075 



100%|███████████████████████████████████████████████████████████████████████████████████████████████████████| 10000/10000 [10:12<00:00, 16.33it/s]


In [13]:
hessian_solver._optimizer_classification

Adam (
Parameter Group 0
    amsgrad: False
    betas: (0.9, 0.999)
    capturable: False
    eps: 1e-08
    foreach: None
    lr: 0.001
    maximize: False
    weight_decay: 0.01
)

In [12]:
classification_model_pretrained = hessian_solver.load_checkpoint_classification(pretrain_ckpt_path)
inv_hessian = hessian_solver.calculate_inv_hessian()


=> loaded checkpoint 'checkpoints/fenchel/mnist/MNIST_2/epoch101_lr0.001_classAll100Each.pt (epoch 0)'
torch.Size([7840])
0 7840
calculating_inv_hessian


LinAlgError: Singular matrix